## Download GeoJSON file for Canadian Provinces and territories

#### https://data.opendatasoft.com/explore/dataset/georef-canada-province%40public/export/?disjunctive.prov_name_en


In [1]:
!wget -O Canada_ShapeFile.geojson 'https://data.opendatasoft.com/api/explore/v2.1/catalog/datasets/georef-canada-province@public/exports/geojson?lang=en&timezone=America%2FNew_York'

--2023-08-06 23:21:07--  https://data.opendatasoft.com/api/explore/v2.1/catalog/datasets/georef-canada-province@public/exports/geojson?lang=en&timezone=America%2FNew_York
Resolving data.opendatasoft.com (data.opendatasoft.com)... 34.249.199.226, 34.248.20.69
Connecting to data.opendatasoft.com (data.opendatasoft.com)|34.249.199.226|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: unspecified [application/json]
Saving to: ‘Canada_ShapeFile.geojson’

Canada_ShapeFile.ge     [   <=>              ] 630.43K  1.44MB/s    in 0.4s    

2023-08-06 23:21:08 (1.44 MB/s) - ‘Canada_ShapeFile.geojson’ saved [645558]



### Fix GeoJSON file so that 'properties.prov_name_en' is a string and not a list

In [2]:
import json
j = open('Canada_ShapeFile.geojson')
data = json.load(j)
j.close()

for i in range(len(data['features'])):
  data['features'][i]['properties']['prov_name_en'] = data['features'][i]['properties']['prov_name_en'][0]

In [3]:
with open('./Canada_ShapeFile.geojson', 'w') as outfile:
    json.dump(data, outfile)

### Get Population data for Canada to test choropleth map

In [4]:
import pandas as pd
df = pd.read_html("https://en.wikipedia.org/wiki/Population_of_Canada_by_province_and_territory")[1]
df = df[~(df['Name']=='Canada')]
df = df[['Name','2021 Census']]
df

Name  2021 Census
0                       Yukon        40232
1        Prince Edward Island       154331
2            British Columbia      5000879
3                     Ontario     14223942
4                    Manitoba      1342153
5                 Nova Scotia       969383
6                     Alberta      4262635
7                      Quebec      8501833
8               New Brunswick       775610
9                Saskatchewan      1132505
10                    Nunavut        36858
11      Northwest Territories        41070
12  Newfoundland and Labrador       510550

### Choropleth Map with Folium library

In [5]:
# import the folium library
import folium

# initialize the map and store it in a m object
m = folium.Map(location=[59.959354, -101.990312], zoom_start=4)

folium.Choropleth(
    geo_data='./Canada_ShapeFile.geojson',
    name="choropleth",
    data=df,
    columns=["Name", "2021 Census"],
    key_on="feature.properties.prov_name_en",
    fill_color="YlGn",
    fill_opacity=0.7,
    line_opacity=.1,
    legend_name="Population - 2021 Census",
).add_to(m)

folium.LayerControl().add_to(m)

m

### Choropleth Map with Plotly library


In [6]:
import plotly.express as px

#df = px.data.election()
#geojson = px.data.election_geojson()

with open('./Canada_ShapeFile.geojson', 'r') as geo:
    mp = json.load(geo)

fig = px.choropleth_mapbox(data_frame=df, geojson=mp, featureidkey="properties.prov_name_en",
                    locations='Name', color='2021 Census',
                    color_continuous_scale="Viridis",
                    #range_color=(0, 14223942),
                    mapbox_style = 'open-street-map',
                    center=dict(lat=59.959354, lon=-101.990312),
                    zoom=2.75,opacity=0.5,
                    #colorbar={"orientation": "h", "x": 0.5, "yanchor": "middle", "y": 0.1}
                   )


#fig.update_geos(fitbounds="locations", visible=False)
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0},
                  coloraxis_colorbar=dict(
                  x=0.01,  # Adjust the x-coordinate (0.0 to 1.0) for horizontal position
                  y=0.5,  # Adjust the y-coordinate (0.0 to 1.0) for vertical position
                  len=0.7,  # Adjust the length of the color bar
                  ))

fig.show()

In [7]:
import plotly.graph_objects as go

with open('./Canada_ShapeFile.geojson', 'r') as geo:
    mp = json.load(geo)

fig = go.Figure(px.choropleth_mapbox(data_frame=df, geojson=mp, featureidkey="properties.prov_name_en",
                    locations='Name', color='2021 Census',
                    color_continuous_scale="Viridis",
                    #range_color=(0, 14223942),
                    mapbox_style = 'carto-positron',
                    center=dict(lat=59.959354, lon=-101.990312),
                    zoom=2.75,opacity=0.5,
                   ))

#fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})

fig.update_layout(
    coloraxis_colorbar=dict(
        x=0.01,  # Adjust the x-coordinate (0.0 to 1.0) for horizontal position
        y=0.5,  # Adjust the y-coordinate (0.0 to 1.0) for vertical position
        len=0.7,  # Adjust the length of the color bar
    ),
    title='Choropleth Map on Mapbox'
    ,margin={"r":0,"t":30,"l":0,"b":0}
)

fig.show()
